In [70]:
import numpy as np
import time
import keras
import pandas as pd
from sklearn.model_selection import train_test_split

In [71]:
X = np.squeeze(np.load('src/smiley_X.npy'))
y = np.load('src/smiley_y.npy')
y = keras.utils.to_categorical(y-1, num_classes = 2)

In [72]:
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=5)


In [73]:
x_train = x_train.reshape(115, 9, 9, 1)
x_test = x_test.reshape(29, 9, 9, 1)
x_train.shape #28*28=784

(115, 9, 9, 1)

In [74]:
model = keras.models.Sequential([
  keras.layers.Conv2D(32, (2,2), activation='relu', input_shape=(9, 9, 1)),
  keras.layers.MaxPooling2D(2, 2),
  keras.layers.Conv2D(32, (2,2), activation='relu'),
  keras.layers.MaxPooling2D(2,2),
  keras.layers.Flatten(),
  keras.layers.Dense(8, activation='relu'),
  keras.layers.Dense(2, activation='softmax')
])
model.compile(optimizer='adam', loss=keras.losses.categorical_crossentropy, metrics=[keras.metrics.categorical_accuracy, keras.metrics.TruePositives(), keras.metrics.FalsePositives(), keras.metrics.TrueNegatives(), keras.metrics.FalseNegatives(), keras.metrics.Precision(), keras.metrics.Recall()])
model.summary()

Model: "sequential_107"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_214 (Conv2D)         (None, 8, 8, 32)          160       
                                                                 
 max_pooling2d_214 (MaxPooli  (None, 4, 4, 32)         0         
 ng2D)                                                           
                                                                 
 conv2d_215 (Conv2D)         (None, 3, 3, 32)          4128      
                                                                 
 max_pooling2d_215 (MaxPooli  (None, 1, 1, 32)         0         
 ng2D)                                                           
                                                                 
 flatten_107 (Flatten)       (None, 32)                0         
                                                                 
 dense_214 (Dense)           (None, 8)              

In [75]:
model.fit(x_train,y_train, epochs=5)
model.evaluate(x_test,y_test)

Epoch 1/5
4/4 [==============================] - 2s 3ms/step - loss: 0.7060 - categorical_accuracy: 0.4696 - true_positives_107: 54.0000 - false_positives_107: 61.0000 - true_negatives_107: 54.0000 - false_negatives_107: 61.0000 - precision_107: 0.4696 - recall_107: 0.4696
Epoch 2/5
4/4 [==============================] - 0s 3ms/step - loss: 0.6764 - categorical_accuracy: 0.4870 - true_positives_107: 56.0000 - false_positives_107: 59.0000 - true_negatives_107: 56.0000 - false_negatives_107: 59.0000 - precision_107: 0.4870 - recall_107: 0.4870
Epoch 3/5
4/4 [==============================] - 0s 3ms/step - loss: 0.6594 - categorical_accuracy: 0.5304 - true_positives_107: 61.0000 - false_positives_107: 54.0000 - true_negatives_107: 61.0000 - false_negatives_107: 54.0000 - precision_107: 0.5304 - recall_107: 0.5304
Epoch 4/5
4/4 [==============================] - 0s 3ms/step - loss: 0.6442 - categorical_accuracy: 0.6522 - true_positives_107: 75.0000 - false_positives_107: 40.0000 - true_neg

[0.5903816223144531,
 0.7241379022598267,
 21.0,
 8.0,
 21.0,
 8.0,
 0.7241379022598267,
 0.7241379022598267]

In [76]:
X = X.reshape(144,9,9,1)

optimisations = [keras.optimizers.SGD, keras.optimizers.RMSprop, keras.optimizers.Adam, keras.optimizers.Nadam]
epochs = [3, 5, 10, 50, 100]
η_list = [0.1, 0.01, 0.001]

In [77]:
from sklearn.model_selection import KFold

run_config_suit = False
file_name = "df_lab11.pkl"
kf = KFold(n_splits = 10)

if run_config_suit:
    start = time.time()
    list_of_results = []
    list_of_crossedevaluated = []
    for opt in optimisations:
        for η in η_list:
            print("\n####################################################################################")
            print("Eta    <Optimisation>")
            print(f"{η} {opt}")
            print("Epoch: [Loss, Accuracy, TP, FP, TN, FN, Precision, Recall]")
            for epoch in epochs:
                model = keras.models.Sequential([
                    keras.layers.Conv2D(32, (2,2), activation='relu', input_shape=(9, 9, 1)),
                    keras.layers.MaxPooling2D(2, 2),
                    keras.layers.Conv2D(32, (2,2), activation='relu'),
                    keras.layers.MaxPooling2D(2,2),
                    keras.layers.Flatten(),
                    keras.layers.Dense(8, activation='relu'),
                    keras.layers.Dense(2, activation='softmax')
                ])
                model.compile(loss=keras.losses.categorical_crossentropy,
                                      optimizer=opt(learning_rate=η),
                                      metrics=[keras.metrics.categorical_accuracy, keras.metrics.TruePositives(), keras.metrics.FalsePositives(), keras.metrics.TrueNegatives(), keras.metrics.FalseNegatives(), keras.metrics.Precision(), keras.metrics.Recall()])

                for train, test in kf.split(X):
                    model.fit(X[train],y[train], epochs=epoch, verbose= 0)
                    result = model.evaluate(X[test],y[test], verbose= 0)
                    list_of_crossedevaluated.append(result)

                config = [opt, η, epoch]

                loss = 0
                acc = 0
                TP = 0
                FP = 0
                TN = 0
                FN = 0
                Precision = 0
                Recall = 0
                for i in list_of_crossedevaluated:
                    loss += i[0]
                    acc += i[1]
                    TP += i[2]
                    FP += i[3]
                    TN += i[4]
                    FN += i[5]
                    Precision += i[6]
                    Recall += i[7]
                result10 = [loss,acc,TP,FP,TN,FN,Precision,Recall]
                result = []
                for i in range(2):
                    result.append(result10[i]/10)
                result.append(TP)
                result.append(FP)
                result.append(TN)
                result.append(FN)
                for i in range(6,8):
                    result.append(result10[i]/10)
                list_of_results.append(result + config)
                list_of_crossedevaluated.clear()
                print(f"\t{epoch}: {result}")

    print("\n\n############## DONE")
    print(time.time() - start)

    labels = ["Loss", "Accuracy", "TP", "FP", "TN", "FN", "Precision", "Recall", "optimiser", "η", "epoch"]
    dfcv = pd.DataFrame(data = list_of_results, columns=labels)
    dfcv.to_pickle(file_name)

else:
    dfcv = pd.read_pickle(file_name)


####################################################################################
Eta    <Optimisation>
0.1 <class 'keras.optimizers.optimizer_v2.gradient_descent.SGD'>
Epoch: [Loss, Accuracy, TP, FP, TN, FN, Precision, Recall]
Epoch 1/3
5/5 [==============================] - 1s 4ms/step - loss: 0.6714 - categorical_accuracy: 0.6124 - true_positives_108: 79.0000 - false_positives_108: 50.0000 - true_negatives_108: 79.0000 - false_negatives_108: 50.0000 - precision_108: 0.6124 - recall_108: 0.6124
Epoch 2/3
5/5 [==============================] - 0s 3ms/step - loss: 0.6681 - categorical_accuracy: 0.5116 - true_positives_108: 66.0000 - false_positives_108: 63.0000 - true_negatives_108: 66.0000 - false_negatives_108: 63.0000 - precision_108: 0.5116 - recall_108: 0.5116
Epoch 3/3
5/5 [==============================] - 0s 3ms/step - loss: 0.6391 - categorical_accuracy: 0.5736 - true_positives_108: 74.0000 - false_positives_108: 55.0000 - true_negatives_108: 74.0000 - false_negatives_108:

In [78]:
dfcv

Loss  Accuracy     TP    FP     TN    FN  Precision    Recall  \
0   1.940798e-01  0.893333  128.0  16.0  128.0  16.0   0.893333  0.893333   
1   2.196966e-01  0.866667  124.0  20.0  124.0  20.0   0.866667  0.866667   
2   6.118993e-02  0.973333  140.0   4.0  140.0   4.0   0.973333  0.973333   
3   8.425102e-04  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
4   2.644450e-04  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
5   6.213477e-01  0.705714  101.0  43.0  101.0  43.0   0.705714  0.705714   
6   6.341320e-01  0.848095  122.0  22.0  122.0  22.0   0.848095  0.848095   
7   4.907898e-01  0.863333  124.0  20.0  124.0  20.0   0.863333  0.863333   
8   8.133217e-02  0.980000  141.0   3.0  141.0   3.0   0.980000  0.980000   
9   3.111081e-02  0.986667  142.0   2.0  142.0   2.0   0.986667  0.986667   
10  6.798909e-01  0.500000   72.0  72.0   72.0  72.0   0.500000  0.500000   
11  6.774130e-01  0.506667   73.0  71.0   73.0  71.0   0.506667  0.506667   
12  6.760748e-01  0.556190   80.0  64.0   80.0  64.0   0.556190  0.556190   
13  6.735450e-01  0.869524  125.0  19.0  125.0  19.0   0.869524  0.869524   
14  3.948685e-01  0.919524  132.0  12.0  132.0  12.0   0.919524  0.919524   
15  7.065201e-01  0.471429   68.0  76.0   68.0  76.0   0.471429  0.471429   
16  8.087633e-01  0.500000   72.0  72.0   72.0  72.0   0.500000  0.500000   
17  7.045987e-01  0.514286   74.0  70.0   74.0  70.0   0.514286  0.514286   
18  7.224033e-01  0.480000   69.0  75.0   69.0  75.0   0.480000  0.480000   
19  7.074413e-01  0.514286   74.0  70.0   74.0  70.0   0.514286  0.514286   
20  2.412483e-01  0.917143  132.0  12.0  132.0  12.0   0.917143  0.917143   
21  1.258199e-02  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
22  1.499204e-03  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
23  5.626620e-07  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
24  0.000000e+00  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
25  3.906637e-01  0.940000  135.0   9.0  135.0   9.0   0.940000  0.940000   
26  2.822736e-01  0.979524  141.0   3.0  141.0   3.0   0.979524  0.979524   
27  1.004532e-01  0.986667  142.0   2.0  142.0   2.0   0.986667  0.986667   
28  3.696465e-04  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
29  6.217289e-05  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
30  7.172235e-01  0.480000   69.0  75.0   69.0  75.0   0.480000  0.480000   
31  7.002933e-01  0.485714   70.0  74.0   70.0  74.0   0.485714  0.485714   
32  6.976015e-01  0.465714   67.0  77.0   67.0  77.0   0.465714  0.465714   
33  6.978967e-01  0.485714   70.0  74.0   70.0  74.0   0.485714  0.485714   
34  6.926138e-01  0.528571   76.0  68.0   76.0  68.0   0.528571  0.528571   
35  6.060945e-02  0.986667  142.0   2.0  142.0   2.0   0.986667  0.986667   
36  2.611808e-02  0.993333  143.0   1.0  143.0   1.0   0.993333  0.993333   
37  7.047791e-02  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
38  1.763291e-05  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
39  1.206335e-05  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
40  3.252211e-01  0.918095  132.0  12.0  132.0  12.0   0.918095  0.918095   
41  2.167152e-01  0.986667  142.0   2.0  142.0   2.0   0.986667  0.986667   
42  1.274322e-01  0.980000  141.0   3.0  141.0   3.0   0.980000  0.980000   
43  2.946095e-03  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
44  6.337016e-04  1.000000  144.0   0.0  144.0   0.0   1.000000  1.000000   
45  6.751220e-01  0.548571   79.0  65.0   79.0  65.0   0.548571  0.548571   
46  7.030301e-01  0.520000   75.0  69.0   75.0  69.0   0.520000  0.520000   
47  7.030768e-01  0.465714   67.0  77.0   67.0  77.0   0.465714  0.465714   
48  6.990800e-01  0.471429   68.0  76.0   68.0  76.0   0.471429  0.471429   
49  2.437678e-01  0.916667  132.0  12.0  132.0  12.0   0.916667  0.916667   
50  5.834215e-02  0.980000  141.0   3.0  141.0   3.0   0.980000  0.980000   
51  1.12

In [79]:
dfcv[dfcv.Accuracy == 1 ]

Loss  Accuracy     TP   FP     TN   FN  Precision  Recall  \
3   8.425102e-04       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
4   2.644450e-04       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
21  1.258199e-02       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
22  1.499204e-03       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
23  5.626620e-07       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
24  0.000000e+00       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
28  3.696465e-04       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
29  6.217289e-05       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
37  7.047791e-02       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
38  1.763291e-05       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
39  1.206335e-05       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
43  2.946095e-03       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
44  6.337016e-04       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
51  1.126782e-02       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
53  2.001464e-05       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
54  1.439797e-06       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
58  2.624604e-03       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
59  4.890744e-02       1.0  144.0  0.0  144.0  0.0        1.0     1.0   

                                            optimiser      η  epoch  
3   <class 'keras.optimizers.optimizer_v2.gradient...  0.100     50  
4   <class 'keras.optimizers.optimizer_v2.gradient...  0.100    100  
21  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.010      5  
22  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.010     10  
23  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.010     50  
24  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.010    100  
28  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.001     50  
29  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.001    100  
37  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.010     10  
38  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.010     50  
39  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.010    100  
43  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.001     50  
44  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.001    100  
51  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.010      5  
53  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.010     50  
54  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.010    100  
58  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.001     50  
59  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.001    100

In [80]:
dfcv[dfcv.Accuracy == 1 ][dfcv.epoch == 5]

C:\Users\barth\AppData\Local\Temp\ipykernel_9292\661620092.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  dfcv[dfcv.Accuracy == 1 ][dfcv.epoch == 5]


Loss  Accuracy     TP   FP     TN   FN  Precision  Recall  \
21  0.012582       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
51  0.011268       1.0  144.0  0.0  144.0  0.0        1.0     1.0   

                                            optimiser     η  epoch  
21  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.01      5  
51  <class 'keras.optimizers.optimizer_v2.nadam.Na...  0.01      5

In [81]:
dfcv[dfcv.Accuracy == 1 ][dfcv.epoch == 10]

C:\Users\barth\AppData\Local\Temp\ipykernel_9292\3942281020.py:1: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  dfcv[dfcv.Accuracy == 1 ][dfcv.epoch == 10]


Loss  Accuracy     TP   FP     TN   FN  Precision  Recall  \
22  0.001499       1.0  144.0  0.0  144.0  0.0        1.0     1.0   
37  0.070478       1.0  144.0  0.0  144.0  0.0        1.0     1.0   

                                            optimiser     η  epoch  
22  <class 'keras.optimizers.optimizer_v2.rmsprop....  0.01     10  
37  <class 'keras.optimizers.optimizer_v2.adam.Adam'>  0.01     10